# This notebook will be used for the capstone project

### Objective
This notebook is used to scrape venues in Zurich, Switzerland and determine where we should open a gym or yoga studio. 

### Neighbourhood data
All neighbourhood data is pulled from wikipedia, with additional manipulation of the data required as the wikipedia data is very inconvenient in this example. So all table rows and columns had to be treated differently. 

### Statistical data of Zurich and neighbourhood borders
Further inhabitant data is collected from the statistical bureau of the city of Zurich. 
The statistical data of the city of Zurich also includes polygon data of the boundaries of individual neighbourhoods. This allows to draw neighbourhood borders and centers (computed from the border polygons) on the map. 

### Collecting gym and yoga studio data
Next, gym and yoga venue data is collected for Zurich. Thanks to the polygon data, we can check if the individual venues are actually located within a given neighbourhood. We can thereby create a very clean dataframe of the neighbourhood locations of each venue. 

### Final assessment
Finally, we can use our statistical inhabitant data to determine in which neighbourhood we have a lot of gyms (people exercising), but not a lot of yoga studios (particular form of exercising). This will help someone to open their yoga studio in a location with demand for physical activity. 

We can also determine neighbourhoods that do not have a lot of gyms or yoga studios per inhabitant. So a new owner of a venue should investigate these neighbourhoods first to check the viability of opening a venue there.

### Import libraries

In [1]:
import pandas as pd
import numpy as np
import re
import requests # library to handle requests
from bs4 import BeautifulSoup
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

print('Investigating the neighbourhoods of Zurich!')

Investigating the neighbourhoods of Zurich!


### Fetch Zurich neighbourhood table from Wiki

In [2]:
## URL of table
zh_url='https://de.wikipedia.org/wiki/Stadtteile_der_Stadt_Zürich'

### get page content and parse
zh_page = requests.get(zh_url).text
zh_parsed = BeautifulSoup(zh_page,'xml')

### find all tables and table rows
zh_table = zh_parsed.findAll('table',{'class':'wikitable sortable'})[1]
zh_table_rows = zh_table.find_all('tr')

### Extract website information from scraped data

In [3]:
data = []
### read our rows from data
for row in zh_table_rows:
    data.append([t.text.strip() for t in row.find_all('td')])

### omit first and last row
data = data[1:-1]
addition = []

## Pre-processing
### Deal with nested table on wiki

In [4]:
### clean nested table rows
for quartier in data:

    ### check if borough is in row, remember for next row
    if quartier[0].find('Kreis') == 0:
        ### space after Kreis XY
        quartier[0] = re.sub(r"([0-9]+(\.[0-9]+)?)",r" \1 ", quartier[0]).strip()
        addition = quartier[0]
    elif quartier[0].find('Kreis') != 0:
        quartier.insert(0, addition) 
    
    ### remove entry of sigil
    if quartier[1] == '':
        del quartier[1]
        
    ### remove non-sensical strings
    for j, ele in enumerate(quartier):
        quartier[j] = re.sub(r'^.*?!', '', ele)

### Read data into dataframe and assign columns

In [5]:
### assign columns to table entries
zh_data = pd.DataFrame(data, columns=['Kreis', 'Quartier', 'BFS-Code', 'Included', 'Area in km²', 'Inhabitants (2018)', 'Inhabitants (2013)', 
 'Inhabitants (2005)', 'Immigrants'])

### convert inhabitant entries
for j, ele in enumerate(zh_data['Inhabitants (2018)']):
    zh_data.loc[j,'Inhabitants (2018)'] = re.sub(r'\'', '', ele)
    
### convert inhabitant entries
for j, ele in enumerate(zh_data['Inhabitants (2013)']):
    zh_data.loc[j,'Inhabitants (2013)'] = re.sub(r'\'', '', ele)
    
### convert inhabitant entries
for j, ele in enumerate(zh_data['Inhabitants (2005)']):
    zh_data.loc[j,'Inhabitants (2005)'] = re.sub(r'\'', '', ele)
    
zh_data.head(34)

Kreis              Quartier BFS-Code  Included  \
0            Kreis  1 Altstadt               Rathaus   261011  vor 1893   
1            Kreis  1 Altstadt           Hochschulen   261012  vor 1893   
2            Kreis  1 Altstadt             Lindenhof   261013  vor 1893   
3            Kreis  1 Altstadt                  City   261014  vor 1893   
4                     Kreis  2           Wollishofen   261021      1893   
5                     Kreis  2              Leimbach   261023      1893   
6                     Kreis  2                  Enge   261024      1893   
7            Kreis  3 Wiedikon          Alt-Wiedikon   261031      1893   
8            Kreis  3 Wiedikon           Friesenberg   261033      1893   
9            Kreis  3 Wiedikon              Sihlfeld   261034      1893   
10         Kreis  4 Aussersihl                  Werd   261041      1893   
11         Kreis  4 Aussersihl           Langstrasse   261042      1893   
12         Kreis  4 Aussersihl                  Hard   261044      1893   
13  Kreis  5 Industriequartier         Gewerbeschule   261051      1893   
14  Kreis  5 Industriequartier           Escher Wyss   261052      1893   
15                    Kreis  6           Unterstrass   261061      1893   
16                    Kreis  6            Oberstrass   261063      1893   
17                    Kreis  7              Fluntern   261071      1893   
18                    Kreis  7             Hottingen   261072      1893   
19                    Kreis  7            Hirslanden   261073      1893   
20                    Kreis  7               Witikon   261074      1934   
21           Kreis  8 Riesbach               Seefeld   261081      1893   
22           Kreis  8 Riesbach             Mühlebach   261082      1893   
23           Kreis  8 Riesbach               Weinegg   261083      1893   
24                    Kreis  9           Albisrieden   261091      1934   
25                    Kreis  9            Altstetten   261092      1934   
26                   Kreis  10                 Höngg   261101      1934   
27                   Kreis  10             Wipkingen   261102      1893   
28                   Kreis  11             Affoltern   261111      1934   
29                   Kreis  11              Oerlikon   261115      1934   
30                   Kreis  11               Seebach   261119      1934   
31    Kreis  12 Schwamendingen               Saatlen   261121      1934   
32    Kreis  12 Schwamendingen  Schwamendingen-Mitte   261122      1934   
33    Kreis  12 Schwamendingen            Hirzenbach   261123      1934   

   Area in km² Inhabitants (2018) Inhabitants (2013) Inhabitants (2005)  \
0         0.38               3267               3194               3081   
1         0.56                664                665                695   
2         0.23                990                923                950   
3         0.64                829                783                846   
4         5.75              18923              15937              15592   
5         2.92               6320               5730               4867   
6         2.40               9634               8836               8375   
7         1.85              17956              16706              14971   
8         5.15              10933              10696              10360   
9         1.64              21680              20931              20554   
10        0.31               4455               4188               3878   
11        1.13              11111              10686              10368   
12        1.46              13163              12715              13241   
13        0.73               9513               9626               9690   
14        1.27               6066               4010               2727   
15        2.46              23394              21876              19921   
16        2.64              10927              10452               9494   
17        2.84               8485               7

## Plotting map
### Load libraries for mapping

In [6]:
from geopy.geocoders import Nominatim

import matplotlib.cm as cm
import matplotlib.colors as colors

import geopandas as gpd
from shapely.geometry import shape
import geojson

import folium

/home/davo/.local/lib/python3.8/site-packages/geopandas/_compat.py:84: UserWarning: The Shapely GEOS version (3.8.0-CAPI-1.13.1 ) is incompatible with the GEOS version PyGEOS was compiled with (3.9.0-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(


### Find Lat/Lon data of Zurich

In [7]:
address = 'ZURICH'

geolocator = Nominatim(user_agent="zurich_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The lati & long coordinate of Zurich are {}, {}.'.format(latitude, longitude))

The lati & long coordinate of Zurich are 47.3744489, 8.5410422.


### Load map of Zurich

In [8]:
zh_map = folium.Map(location=[latitude, longitude], zoom_start=12)
# zh_map

### Load polygons of neighbourhoods 

In [9]:
### load polygon data for quartiere/neighbourhoods
zh_geo = gpd.read_file('stzh.adm_statistische_quartiere_map.shp')  
### rename borough/kreis and neighbourhood/quartier
zh_geo.rename(columns = {'qname':'Quartier','kname':'Kreis'}, inplace = True) 
### convert to lat/lon
gjson = zh_geo.to_crs(epsg='4326').to_json()
### add polygons to map
folium.GeoJson(gjson).add_to(zh_map)
zh_map
zh_geo

objectid objid    qnr              Quartier   knr     Kreis  \
0          1    34   73.0            Hirslanden   7.0   Kreis 7   
1          2    33   83.0               Weinegg   8.0   Kreis 8   
2          3    32   82.0            MÃ¼hlebach   8.0   Kreis 8   
3          4    31   81.0               Seefeld   8.0   Kreis 8   
4          7    16   41.0                  Werd   4.0   Kreis 4   
5          8    15   34.0              Sihlfeld   3.0   Kreis 3   
6          9    14   91.0           Albisrieden   9.0   Kreis 9   
7         10    13   72.0             Hottingen   7.0   Kreis 7   
8          5    30   21.0           Wollishofen   2.0   Kreis 2   
9         18    22   61.0           Unterstrass   6.0   Kreis 6   
10        19    20  101.0                HÃ¶ngg  10.0  Kreis 10   
11        20    19  115.0              Oerlikon  11.0  Kreis 11   
12        21    18  111.0             Affoltern  11.0  Kreis 11   
13         6    29   23.0              Leimbach   2.0   Kreis 2   
14        11    28   24.0                  Enge   2.0   Kreis 2   
15        34     1   51.0         Gewerbeschule   5.0   Kreis 5   
16        12    26   42.0           Langstrasse   4.0   Kreis 4   
17        13    27   52.0           Escher Wyss   5.0   Kreis 5   
18        14    25   74.0               Witikon   7.0   Kreis 7   
19        15    24   44.0                  Hard   4.0   Kreis 4   
20        16    23   13.0             Lindenhof   1.0   Kreis 1   
21        17    21  102.0             Wipkingen  10.0  Kreis 10   
22        22    17   14.0                  City   1.0   Kreis 1   
23        23    12   11.0               Rathaus   1.0   Kreis 1   
24        24    11   71.0              Fluntern   7.0   Kreis 7   
25        25    10   63.0            Oberstrass   6.0   Kreis 6   
26        26     9  121.0               Saatlen  12.0  Kreis 12   
27        27     8  119.0               Seebach  11.0  Kreis 11   
28        28     7   33.0           Friesenberg   3.0   Kreis 3   
29        29     6   12.0           Hochschulen   1.0   Kreis 1   
30        30     5   92.0            Altstetten   9.0   Kreis 9   
31        31     4  123.0            Hirzenbach  12.0  Kreis 12   
32        32     3  122.0  Schwamendingen-Mitte  12.0  Kreis 12   
33        33     2   31.0          Alt-Wiedikon   3.0   Kreis 3   

                                             geometry  
0   POLYGON ((2684457.034 1246514.804, 2684466.315...  
1   POLYGON ((2684457.383 1246512.719, 2684458.291...  
2   POLYGON ((2684269.913 1246566.796, 2684271.618...  
3   POLYGON ((2683794.254 1246609.895, 2683802.117...  
4   POLYGON ((2682651.888 1247587.653, 2682650.697...  
5   POLYGON ((2681620.924 1247666.669, 2681627.848...  
6   POLYGON ((2680246.801 1248184.959, 2680242.274...  
7   POLYGON ((2686439.052 1249239.332, 2686493.549...  
8   POLYGON ((2683464.971 1243316.936, 2683455.914...  
9   POLYGON ((2682138.424 1251265.833, 2682137.008...  
10  POLYGON ((2682028.720 1251162.806, 2682034.672...  
11  POLYGON ((2683703.812 1250431.281, 2683704.022...  
12  POLYGON ((2682556.567 1252286.961, 2682548.119...  
13  POLYGON ((2681571.990 1244270.941, 2681565.666...  
14  POLYGON ((2682901.036 1245161.795, 2682834.117...  
15  POLYGON ((2682685.041 1248920.675, 2682876.773...  
16  POLYGON ((2681465.865 1248839.333, 2681465.123...  
17  POLYGON ((2681459.605 1248841.725, 2681440.529...  
18  POLYGON ((2687854.738 1247430.737, 2687856.523...  
19  POLYGON ((2681365.838 1248684.186, 2681460.264...  
20  POLYGON ((2683168.047 1246706.173, 2683187.786...  
21  POLYGON ((2682160.984 1251221.358, 2682183.009...  
22  POLYGON ((2683325.312 1247912.255, 2683325.292...  
23  POLYGON ((2683374.124 1246786.080, 2683374.192...  
24  POLYGON ((2686340.748 1249189.459, 2686329.721...  
25  POLYGON ((2685281.256 1249561.546, 2685223.699...  
26  POLYGON ((2684869.209 1252256.173, 2684928.016...  
27  POLYGON ((2682176.731 1254103.495, 2682261.272...  
28  POLYGON ((2681661.702 1245051.

### Obtain quartier/neighbourhood centroids from circumference polygons

In [10]:
### convert from swiss encoding to lat/lon
zh_poly = zh_geo.to_crs(epsg='4326')

### initialize polygon centroids
lat_centroid = []
lon_centroid = []

### loop through quartiers/neighbourhoods
for i in range(len(zh_poly)):
    ### convert to shape object
    p = shape(zh_poly['geometry'][i])
    ### extract polygon points
    lon_polygon, lat_polygon = p.exterior.coords.xy
    
    ### initialize centroid for each polygon
    lat = 0
    lon = 0
    ### add up all points
    for j in range(len(lon_polygon)):
        lat += lat_polygon[j]
        lon += lon_polygon[j]

    ### final coordinates
    lat_centroid.append(lat/len(lat_polygon))
    lon_centroid.append(lon/len(lon_polygon))

# quartier centroid lat/lon coordinates
zh_geo['Latitude'] = lat_centroid
zh_geo['Longitude'] = lon_centroid

zh_geo.head()

objectid objid   qnr    Quartier  knr    Kreis  \
0         1    34  73.0  Hirslanden  7.0  Kreis 7   
1         2    33  83.0     Weinegg  8.0  Kreis 8   
2         3    32  82.0  MÃ¼hlebach  8.0  Kreis 8   
3         4    31  81.0     Seefeld  8.0  Kreis 8   
4         7    16  41.0        Werd  4.0  Kreis 4   

                                            geometry   Latitude  Longitude  
0  POLYGON ((2684457.034 1246514.804, 2684466.315...  47.362020   8.572849  
1  POLYGON ((2684457.383 1246512.719, 2684458.291...  47.356528   8.567511  
2  POLYGON ((2684269.913 1246566.796, 2684271.618...  47.358239   8.556874  
3  POLYGON ((2683794.254 1246609.895, 2683802.117...  47.357012   8.554880  
4  POLYGON ((2682651.888 1247587.653, 2682650.697...  47.372574   8.526534

### Visualize all Zurich neighbourhood centroids

In [11]:
# add quartier markers to map
for lat, lon, neighbourhood, kreis in zip(zh_geo['Latitude'], zh_geo['Longitude'], zh_geo['Quartier'], zh_geo['Kreis']):
    label = '{} , {}'.format(kreis, neighbourhood)
    label = folium.Popup(label)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='blue',
        fill=False
    ).add_to(zh_map)  
    
zh_map

In [12]:
zh_data = zh_data.merge(zh_geo.drop(columns=['Kreis']), left_on='Quartier', right_on='Quartier')
zh_data.head()

Kreis     Quartier BFS-Code  Included Area in km²  \
0  Kreis  1 Altstadt      Rathaus   261011  vor 1893        0.38   
1  Kreis  1 Altstadt  Hochschulen   261012  vor 1893        0.56   
2  Kreis  1 Altstadt    Lindenhof   261013  vor 1893        0.23   
3  Kreis  1 Altstadt         City   261014  vor 1893        0.64   
4           Kreis  2  Wollishofen   261021      1893        5.75   

  Inhabitants (2018) Inhabitants (2013) Inhabitants (2005) Immigrants  \
0               3267               3194               3081     30,1 %   
1                664                665                695     34,3 %   
2                990                923                950     30,1 %   
3                829                783                846     30,0 %   
4              18923              15937              15592     29,1 %   

   objectid objid   qnr  knr  \
0        23    12  11.0  1.0   
1        29     6  12.0  1.0   
2        16    23  13.0  1.0   
3        22    17  14.0  1.0   
4         5    30  21.0  2.0   

                                            geometry   Latitude  Longitude  
0  POLYGON ((2683374.124 1246786.080, 2683374.192...  47.370203   8.543717  
1  POLYGON ((2683993.543 1247428.241, 2683993.817...  47.372247   8.545615  
2  POLYGON ((2683168.047 1246706.173, 2683187.786...  47.369930   8.541478  
3  POLYGON ((2683325.312 1247912.255, 2683325.292...  47.373650   8.537898  
4  POLYGON ((2683464.971 1243316.936, 2683455.914...  47.339905   8.528241

### Look at downtown Zurich

In [13]:
### kreis 1 is "downtown" Zurich
address = 'Kreis 1 ZURICH'

### locate the above address
geolocator = Nominatim(user_agent="zurich_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The lati & long coordinate of Downtown Zurich (Kreis 1) are {}, {}.'.format(latitude, longitude))

The lati & long coordinate of Downtown Zurich (Kreis 1) are 47.3722329, 8.5423291.


### Visualizing and clustering of downtown/center Zurich

In [14]:
zh_center = zh_data[zh_data['Kreis'].str.contains('1 ')].reset_index(drop=True)
zh_center.head()

# create map of T using latitude and longitude values
zh_map_center = folium.Map(location=[latitude, longitude], zoom_start=13)

# add markers to map
for lat, lng, label in zip(zh_center['Latitude'], zh_center['Longitude'], zh_center['Quartier']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=False,
        parse_html=False).add_to(zh_map_center)  

### look at kreis 1/center only
zh_geo_center = zh_geo[zh_geo['Kreis'] == 'Kreis 1']
### convert to lat/lon
gjson_center = zh_geo_center.to_crs(epsg='4326').to_json()
### add polygons to map
folium.GeoJson(gjson_center).add_to(zh_map_center)

zh_map_center

### Load Foursquare info

In [15]:
CLIENT_ID = 'DO2DZ0V5ZCOSSAOPBBBOP1GDPMUFVVYG55UV45DQOFELBZTH' # your Foursquare ID
CLIENT_SECRET = '1PIX4SXCFIEKXPV5JPGYN3GCDLANHLFLO2L0MYRDBRGW44RD' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: DO2DZ0V5ZCOSSAOPBBBOP1GDPMUFVVYG55UV45DQOFELBZTH
CLIENT_SECRET:1PIX4SXCFIEKXPV5JPGYN3GCDLANHLFLO2L0MYRDBRGW44RD


## Explore first neighbourhood as example (Quartier 1: Rathaus)

Extract name of the first neighbourhood/quartier

In [16]:
zh_data.loc[0, 'Quartier']

'Rathaus'

Set location data for first neighbourhood

In [17]:
neighborhood_latitude = zh_data.loc[0, 'Latitude']
neighborhood_longitude = zh_data.loc[0, 'Longitude'] 

neighborhood_name = zh_data.loc[0, 'Quartier'] 

print('Latitude and longitude values of Quartier {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Quartier Rathaus are 47.37020335236508, 8.54371726189494.


## Check top 100 venues of first neighbourhood

In [18]:
### number of venues
LIMIT = 100 
radius = 1000 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url 

'https://api.foursquare.com/v2/venues/explore?&client_id=DO2DZ0V5ZCOSSAOPBBBOP1GDPMUFVVYG55UV45DQOFELBZTH&client_secret=1PIX4SXCFIEKXPV5JPGYN3GCDLANHLFLO2L0MYRDBRGW44RD&v=20180605&ll=47.37020335236508,8.54371726189494&radius=1000&limit=100'

Output the result found for the first neighbourhood

In [19]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '602adf9a3e9575501b5e5b93'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Kreis 1',
  'headerFullLocation': 'Kreis 1, Zürich',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 238,
  'suggestedBounds': {'ne': {'lat': 47.37920336136509,
    'lng': 8.556981329452189},
   'sw': {'lat': 47.36120334336507, 'lng': 8.530453194337692}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b463772f964a5205c1a26e3',
       'name': 'Fitnesspark Münstergasse',
       'location': {'address': 'Blaufahnenstr. 3',
        'lat': 47.37088805140556,
        'lng': 8.544999004166998,
        'labeledLatLngs': [{'label': 'display',
          'lat': 47

### function that extracts the category of the venue


In [20]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [21]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-21-561c05f0fdd1>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name            categories        lat       lng
0     Fitnesspark Münstergasse  Gym / Fitness Center  47.370888  8.544999
1                 Café Schober                  Café  47.371400  8.544149
2  Schwarzenbach Kolonialwaren          Gourmet Shop  47.371444  8.544091
3                Ban Song Thai       Thai Restaurant  47.369395  8.544136
4                   barfussbar                   Bar  47.368441  8.542181

In [22]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


## 2. Explore Neighbourhoods/Quartiere in Zurich


In [23]:
def getNearbyVenues(names, latitudes, longitudes, radius=2000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print('Scraping venues for quartier:', name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [24]:
zh_venues = getNearbyVenues(names=zh_data['Quartier'],
                                   latitudes=zh_data['Latitude'],
                                   longitudes=zh_data['Longitude']
                                  )

Scraping venues for quartier: Rathaus
Scraping venues for quartier: Hochschulen
Scraping venues for quartier: Lindenhof
Scraping venues for quartier: City
Scraping venues for quartier: Wollishofen
Scraping venues for quartier: Leimbach
Scraping venues for quartier: Enge
Scraping venues for quartier: Alt-Wiedikon
Scraping venues for quartier: Friesenberg
Scraping venues for quartier: Sihlfeld
Scraping venues for quartier: Werd
Scraping venues for quartier: Langstrasse
Scraping venues for quartier: Hard
Scraping venues for quartier: Gewerbeschule
Scraping venues for quartier: Escher Wyss
Scraping venues for quartier: Unterstrass
Scraping venues for quartier: Oberstrass
Scraping venues for quartier: Fluntern
Scraping venues for quartier: Hottingen
Scraping venues for quartier: Hirslanden
Scraping venues for quartier: Witikon
Scraping venues for quartier: Seefeld
Scraping venues for quartier: Weinegg
Scraping venues for quartier: Albisrieden
Scraping venues for quartier: Altstetten
Scrapin

In [25]:
print(zh_venues.shape)
zh_venues.head()

(2866, 7)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0       Rathaus               47.370203                 8.543717   
1       Rathaus               47.370203                 8.543717   
2       Rathaus               47.370203                 8.543717   
3       Rathaus               47.370203                 8.543717   
4       Rathaus               47.370203                 8.543717   

                         Venue  Venue Latitude  Venue Longitude  \
0     Fitnesspark Münstergasse       47.370888         8.544999   
1                 Café Schober       47.371400         8.544149   
2  Schwarzenbach Kolonialwaren       47.371444         8.544091   
3                   barfussbar       47.368441         8.542181   
4                     Old Crow       47.372092         8.541024   

         Venue Category  
0  Gym / Fitness Center  
1                  Café  
2          Gourmet Shop  
3                   Bar  
4          Cocktail Bar

In [26]:
zh_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  Neighbourhood Longitude  Venue  \
Neighbourhood                                                                  
Affoltern                                 40                       40     40   
Albisrieden                               88                       88     88   
Alt-Wiedikon                             100                      100    100   
Altstetten                                94                       94     94   
City                                     100                      100    100   
Enge                                     100                      100    100   
Escher Wyss                              100                      100    100   
Fluntern                                 100                      100    100   
Friesenberg                               83                       83     83   
Gewerbeschule                            100                      100    100   
Hard                                     100                      100    100   
Hirslanden                               100                      100    100   
Hirzenbach                                90                       90     90   
Hochschulen                              100                      100    100   
Hottingen                                 90                       90     90   
Langstrasse                              100                      100    100   
Leimbach                                  24                       24     24   
Lindenhof                                100                      100    100   
Oberstrass                               100                      100    100   
Oerlikon                                 100                      100    100   
Rathaus                                  100                      100    100   
Saatlen                                  100                      100    100   
Schwamendingen-Mitte                      88                       88     88   
Seebach                                  100                      100    100   
Seefeld                                  100                      100    100   
Sihlfeld                                 100                      100    100   
Unterstrass                              100                      100    100   
Weinegg                                  100                      100    100   
Werd                                     100                      100    100   
Wipkingen                                100                      100    100   
Witikon                                   17                       17     17   
Wollishofen                               52                       52     52   

                      Venue Latitude  Venue Longitude  Venue Category  
Neighbourhood                                                          
Affoltern                         40               40              40  
Albisrieden                       88               88              88  
Alt-Wiedikon                     100              100             100  
Altstetten                        94               94              94  
City                             100              100             100  
Enge                             100              100             100  
Escher Wyss                      100              100             100  
Fluntern                         100              100             100  
Friesenberg                       83               83              83  
Gewerbeschule                    100              100             100  
Hard                             100              100             100  
Hirslanden                       100              100             100  
Hirzenbach                        90               90              90  
Hochschulen                      100              100             100  
Hottingen                         90               90              90  
Langstrasse                      100              100             100  
Leimb

In [27]:
print('There are {} uniques categories.'.format(len(zh_venues['Venue Category'].unique())))

There are 196 uniques categories.


## Look into specific category

In [28]:
### number of venues
LIMIT = 50
radius = 2000 # define radius

def getNearbyVenuesCategory(names, latitudes, longitudes, foursquare_category_id, radius=2000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print('Scraping venues for quartier:', name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT,
            foursquare_category_id)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']

        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Extract specific categories

In [29]:
foursquare_id_yoga = '4bf58dd8d48988d102941735'
foursquare_id_gym = '4bf58dd8d48988d175941735'

zh_venues_yoga = getNearbyVenuesCategory(names=zh_data['Quartier'],
                                   latitudes=zh_data['Latitude'],
                                   longitudes=zh_data['Longitude'],
                                   foursquare_category_id=foursquare_id_yoga
                                  )

zh_venues_gym = getNearbyVenuesCategory(names=zh_data['Quartier'],
                                   latitudes=zh_data['Latitude'],
                                   longitudes=zh_data['Longitude'],
                                   foursquare_category_id=foursquare_id_gym
                                  )

zh_venues_yoga.head(100)
zh_venues_gym.head(400)

Scraping venues for quartier: Rathaus
Scraping venues for quartier: Hochschulen
Scraping venues for quartier: Lindenhof
Scraping venues for quartier: City
Scraping venues for quartier: Wollishofen
Scraping venues for quartier: Leimbach
Scraping venues for quartier: Enge
Scraping venues for quartier: Alt-Wiedikon
Scraping venues for quartier: Friesenberg
Scraping venues for quartier: Sihlfeld
Scraping venues for quartier: Werd
Scraping venues for quartier: Langstrasse
Scraping venues for quartier: Hard
Scraping venues for quartier: Gewerbeschule
Scraping venues for quartier: Escher Wyss
Scraping venues for quartier: Unterstrass
Scraping venues for quartier: Oberstrass
Scraping venues for quartier: Fluntern
Scraping venues for quartier: Hottingen
Scraping venues for quartier: Hirslanden
Scraping venues for quartier: Witikon
Scraping venues for quartier: Seefeld
Scraping venues for quartier: Weinegg
Scraping venues for quartier: Albisrieden
Scraping venues for quartier: Altstetten
Scrapin

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0         Rathaus               47.370203                 8.543717   
1         Rathaus               47.370203                 8.543717   
2         Rathaus               47.370203                 8.543717   
3         Rathaus               47.370203                 8.543717   
4         Rathaus               47.370203                 8.543717   
..            ...                     ...                      ...   
395          Hard               47.381404                 8.512116   
396          Hard               47.381404                 8.512116   
397          Hard               47.381404                 8.512116   
398          Hard               47.381404                 8.512116   
399          Hard               47.381404                 8.512116   

                              Venue  Venue Latitude  Venue Longitude  \
0          Fitnesspark Münstergasse       47.370888         8.544999   
1                            Indigo       47.372532         8.534018   
2     Migros Fitnesspark Stockerhof       47.366313         8.535020   
3                Balboa Bar and Gym       47.373542         8.533390   
4                 Luxor Sports Club       47.367976         8.537466   
..                              ...             ...              ...   
395  Gym @ Renaissance Zurich Tower       47.388064         8.514600   
396                     Bikram Yoga       47.373539         8.524790   
397                          Balboa       47.386494         8.522711   
398                Sheraton Fitness       47.390394         8.510223   
399           JAY PERSONAL TRAINING       47.392180         8.512970   

           Venue Category  
0    Gym / Fitness Center  
1    Gym / Fitness Center  
2    Gym / Fitness Center  
3                     Gym  
4                     Gym  
..                    ...  
395  Gym / Fitness Center  
396           Yoga Studio  
397  Gym / Fitness Center  
398  Gym / Fitness Center  
399  Gym / Fitness Center  

[400 rows x 7 columns]

### Check if venue is actually in quartier/neighbourhood

In [30]:
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon

### initialize array of venues not actually in quartier
not_in_quartier = []

### Go through all venues
for i in range(len(zh_venues_yoga['Venue'])):

    quartier_polygon = zh_poly[ zh_poly['Quartier'] == zh_venues_yoga.loc[i, 'Neighbourhood'] ].reset_index(drop=True)
    
    lat = zh_venues_yoga.loc[i, 'Venue Latitude']
    lon = zh_venues_yoga.loc[i, 'Venue Longitude']
    point = Point([lon, lat])
    
    in_quartier = quartier_polygon.contains(point)

    ### store row index if venue is not in quartier
    if in_quartier[0] == False: 
        not_in_quartier.append(i)
        
zh_venues_yoga_checked = zh_venues_yoga.drop(not_in_quartier)

zh_venues_yoga_checked.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0        Rathaus               47.370203                 8.543717   
2        Rathaus               47.370203                 8.543717   
38          City               47.373650                 8.537898   
49   Wollishofen               47.339905                 8.528241   
54          Enge               47.358245                 8.530040   

             Venue  Venue Latitude  Venue Longitude Venue Category  
0          AirYoga       47.368315         8.545928    Yoga Studio  
2         athayoga       47.370736         8.545406    Yoga Studio  
38  PowerQiBalance       47.373033         8.532857    Yoga Studio  
49      SAMiRAYOGA       47.344446         8.526638    Yoga Studio  
54     Planet Yoga       47.365101         8.525203    Yoga Studio

## Map of checked venues

In [31]:
columns_to_drop = ['Neighbourhood Latitude', 'Neighbourhood Longitude', 'Venue Latitude', 'Venue Longitude', 'Venue Category']

zh_venues_total_yoga = zh_venues_yoga.groupby('Neighbourhood').count().drop(columns=columns_to_drop)
zh_venues_total_gym = zh_venues_gym.groupby('Neighbourhood').count().drop(columns=columns_to_drop)

### merge yoga and gym df
zh_venues_total_comparison = zh_venues_total_yoga.merge(zh_venues_total_gym, left_on='Neighbourhood', right_on='Neighbourhood', suffixes=('_yoga', '_gym'))
### determine ratio of gyms to yoga studio
zh_venues_total_comparison['Gym/Yoga'] = zh_venues_total_comparison['Venue_gym'].div(zh_venues_total_comparison['Venue_yoga'], axis=0).round(2)
### merge in inhabitant data
zh_venues_total_comparison = zh_venues_total_comparison.merge(zh_data[['Quartier', 'Inhabitants (2018)']], left_on='Neighbourhood', right_on='Quartier').set_index('Quartier')

### convert inhabitant column type to int
zh_venues_total_comparison['Inhabitants (2018)'] = zh_venues_total_comparison['Inhabitants (2018)'].astype(int)

### determine ratio of inhabitants to yoga
zh_venues_total_comparison['pp_yoga'] = zh_venues_total_comparison['Inhabitants (2018)'].div(zh_venues_total_comparison['Venue_yoga'], axis=0).round(1)
### determine ratio of inhabitants to gym
zh_venues_total_comparison['pp_gym'] = zh_venues_total_comparison['Inhabitants (2018)'].div(zh_venues_total_comparison['Venue_gym'], axis=0).round(1)

zh_venues_total_comparison.head(34)


Venue_yoga  Venue_gym  Gym/Yoga  Inhabitants (2018)  \
Quartier                                                                    
Affoltern                      3          4      1.33               26562   
Albisrieden                    3         11      3.67               22304   
Alt-Wiedikon                   5         29      5.80               17956   
Altstetten                     2         13      6.50               33461   
City                          13         47      3.62                 829   
Enge                           9         29      3.22                9634   
Escher Wyss                    6         39      6.50                6066   
Fluntern                       4         17      4.25                8485   
Friesenberg                    3          8      2.67               10933   
Gewerbeschule                 11         48      4.36                9513   
Hard                           9         42      4.67               13163   
Hirslanden                     2          7      3.50                7488   
Hirzenbach                     1          5      5.00               12801   
Hochschulen                   12         41      3.42                 664   
Hottingen                      4          8      2.00               11265   
Langstrasse                   13         50      3.85               11111   
Leimbach                       2          4      2.00                6320   
Lindenhof                     12         44      3.67                 990   
Oberstrass                     6         22      3.67               10927   
Oerlikon                       2         16      8.00               23214   
Rathaus                       12         42      3.50                3267   
Saatlen                        4         12      3.00                8582   
Schwamendingen-Mitte           1          4      4.00               11100   
Seebach                        4         13      3.25               25568   
Seefeld                        4         15      3.75                5253   
Sihlfeld                       6         36      6.00               21680   
Unterstrass                    4         25      6.25               23394   
Weinegg                        3          9      3.00                5220   
Werd                          12         50      4.17                4455   
Wipkingen                      5         26      5.20               16321   
Wollishofen                    1          3      3.00               18923   

                      pp_yoga  pp_gym  
Quartier                               
Affoltern              8854.0  6640.5  
Albisrieden            7434.7  2027.6  
Alt-Wiedikon           3591.2   619.2  
Altstetten            16730.5  2573.9  
City                     63.8    17.6  
Enge                   1070.4   332.2  
Escher Wyss            1011.0   155.5  
Fluntern               2121.2   499.1  
Friesenberg            3644.3  1366.6  
Gewerbeschule           864.8   198.2  
Hard                   1462.6   313.4  
Hirslanden             3744.0  1069.7  
Hirzenbach            12801.0  2560.2  
Hochschulen              55.3    16.2  
Hottingen              2816.2  1408.1  
Langstrasse             854.7   222.2  
Leimbach               3160.0  1580.0  
Lindenhof                82.5    22.5  
Oberstrass             1821.2   496.7  
Oerlikon              11607.0  1450.9  
Rathaus                 272.2    77.8  
Saatlen                2145.5   715.2  
Schwamendingen-Mitte  11100.0  2775.0  
Seebach                6392.0  1966.8  
Seefeld                1313.2   350.2  
Sihlfeld               3613.3   602.2  
Unterstrass            5848.5   935.8  
Weinegg                1740.0   580.0  
Werd                    371.2    89.1  
Wipkingen              3264.2   627.7  
Wollishofen           18923.0  6307.7

In [32]:
# add yoga markers to map
for lat, lng, label in zip(zh_venues_yoga['Venue Latitude'], zh_venues_yoga['Venue Longitude'], zh_venues_yoga['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=False,
        parse_html=False).add_to(zh_map)  
    
# add gym markers to map
for lat, lng, label in zip(zh_venues_gym['Venue Latitude'], zh_venues_gym['Venue Longitude'], zh_venues_gym['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='green',
        fill=False,
        parse_html=False).add_to(zh_map) 

zh_map

### Count Yoga studios and gyms per neighbourhood

In [33]:
zh_venues_total_comparison.sort_values(by=['pp_yoga'],ascending=False).head(34)

Venue_yoga  Venue_gym  Gym/Yoga  Inhabitants (2018)  \
Quartier                                                                    
Wollishofen                    1          3      3.00               18923   
Altstetten                     2         13      6.50               33461   
Hirzenbach                     1          5      5.00               12801   
Oerlikon                       2         16      8.00               23214   
Schwamendingen-Mitte           1          4      4.00               11100   
Affoltern                      3          4      1.33               26562   
Albisrieden                    3         11      3.67               22304   
Seebach                        4         13      3.25               25568   
Unterstrass                    4         25      6.25               23394   
Hirslanden                     2          7      3.50                7488   
Friesenberg                    3          8      2.67               10933   
Sihlfeld                       6         36      6.00               21680   
Alt-Wiedikon                   5         29      5.80               17956   
Wipkingen                      5         26      5.20               16321   
Leimbach                       2          4      2.00                6320   
Hottingen                      4          8      2.00               11265   
Saatlen                        4         12      3.00                8582   
Fluntern                       4         17      4.25                8485   
Oberstrass                     6         22      3.67               10927   
Weinegg                        3          9      3.00                5220   
Hard                           9         42      4.67               13163   
Seefeld                        4         15      3.75                5253   
Enge                           9         29      3.22                9634   
Escher Wyss                    6         39      6.50                6066   
Gewerbeschule                 11         48      4.36                9513   
Langstrasse                   13         50      3.85               11111   
Werd                          12         50      4.17                4455   
Rathaus                       12         42      3.50                3267   
Lindenhof                     12         44      3.67                 990   
City                          13         47      3.62                 829   
Hochschulen                   12         41      3.42                 664   

                      pp_yoga  pp_gym  
Quartier                               
Wollishofen           18923.0  6307.7  
Altstetten            16730.5  2573.9  
Hirzenbach            12801.0  2560.2  
Oerlikon              11607.0  1450.9  
Schwamendingen-Mitte  11100.0  2775.0  
Affoltern              8854.0  6640.5  
Albisrieden            7434.7  2027.6  
Seebach                6392.0  1966.8  
Unterstrass            5848.5   935.8  
Hirslanden             3744.0  1069.7  
Friesenberg            3644.3  1366.6  
Sihlfeld               3613.3   602.2  
Alt-Wiedikon           3591.2   619.2  
Wipkingen              3264.2   627.7  
Leimbach               3160.0  1580.0  
Hottingen              2816.2  1408.1  
Saatlen                2145.5   715.2  
Fluntern               2121.2   499.1  
Oberstrass             1821.2   496.7  
Weinegg                1740.0   580.0  
Hard                   1462.6   313.4  
Seefeld                1313.2   350.2  
Enge                   1070.4   332.2  
Escher Wyss            1011.0   155.5  
Gewerbeschule           864.8   198.2  
Langstrasse             854.7   222.2  
Werd                    371.2    89.1  
Rathaus                 272.2    77.8  
Lindenhof                82.5    22.5  
City                     63.8    17.6  
Hochschulen              55.3    16.2

In [34]:
zh_venues_total_comparison.sort_values(by=['pp_gym'],ascending=False).head(34)

Venue_yoga  Venue_gym  Gym/Yoga  Inhabitants (2018)  \
Quartier                                                                    
Affoltern                      3          4      1.33               26562   
Wollishofen                    1          3      3.00               18923   
Schwamendingen-Mitte           1          4      4.00               11100   
Altstetten                     2         13      6.50               33461   
Hirzenbach                     1          5      5.00               12801   
Albisrieden                    3         11      3.67               22304   
Seebach                        4         13      3.25               25568   
Leimbach                       2          4      2.00                6320   
Oerlikon                       2         16      8.00               23214   
Hottingen                      4          8      2.00               11265   
Friesenberg                    3          8      2.67               10933   
Hirslanden                     2          7      3.50                7488   
Unterstrass                    4         25      6.25               23394   
Saatlen                        4         12      3.00                8582   
Wipkingen                      5         26      5.20               16321   
Alt-Wiedikon                   5         29      5.80               17956   
Sihlfeld                       6         36      6.00               21680   
Weinegg                        3          9      3.00                5220   
Fluntern                       4         17      4.25                8485   
Oberstrass                     6         22      3.67               10927   
Seefeld                        4         15      3.75                5253   
Enge                           9         29      3.22                9634   
Hard                           9         42      4.67               13163   
Langstrasse                   13         50      3.85               11111   
Gewerbeschule                 11         48      4.36                9513   
Escher Wyss                    6         39      6.50                6066   
Werd                          12         50      4.17                4455   
Rathaus                       12         42      3.50                3267   
Lindenhof                     12         44      3.67                 990   
City                          13         47      3.62                 829   
Hochschulen                   12         41      3.42                 664   

                      pp_yoga  pp_gym  
Quartier                               
Affoltern              8854.0  6640.5  
Wollishofen           18923.0  6307.7  
Schwamendingen-Mitte  11100.0  2775.0  
Altstetten            16730.5  2573.9  
Hirzenbach            12801.0  2560.2  
Albisrieden            7434.7  2027.6  
Seebach                6392.0  1966.8  
Leimbach               3160.0  1580.0  
Oerlikon              11607.0  1450.9  
Hottingen              2816.2  1408.1  
Friesenberg            3644.3  1366.6  
Hirslanden             3744.0  1069.7  
Unterstrass            5848.5   935.8  
Saatlen                2145.5   715.2  
Wipkingen              3264.2   627.7  
Alt-Wiedikon           3591.2   619.2  
Sihlfeld               3613.3   602.2  
Weinegg                1740.0   580.0  
Fluntern               2121.2   499.1  
Oberstrass             1821.2   496.7  
Seefeld                1313.2   350.2  
Enge                   1070.4   332.2  
Hard                   1462.6   313.4  
Langstrasse             854.7   222.2  
Gewerbeschule           864.8   198.2  
Escher Wyss            1011.0   155.5  
Werd                    371.2    89.1  
Rathaus                 272.2    77.8  
Lindenhof                82.5    22.5  
City                     63.8    17.6  
Hochschulen              55.3    16.2

## Final assessment

### Per capita
Based on above analysis. The parts of town:
- Affoltern, 
- Wollishofen, 
- Schwamendingen-Mitte and
- Sihlfeld
would be most conducive to open a gym or yoga studio, as their population is very high and the count of gym or yoga venues is very low.

Especially for Sihlfeld, which is very centrally located. 

### Ratio of gym to yoga studios
It is noticeable that the centrally located neighbourhoods all have high ratios if gyms to yoga studios. This could be caused by a high demand for gyms right after work, before work or during lunch. Neighbourhoods further away from the city center often have a lower gym to yoga studio ratio, although they tend to have fewer of both, so those statistics must be treated with caution. Generally, neighbourhoods such as Oerlikon or Weinegg (each with a ratio of 5) seem to have a lot of demand for active venues, but not many yoga studios. So these neighbourhoods should be investigated first when opening a Yoga studio. 